In [1492]:
import pandas as pd
from tqdm.notebook import tqdm
from statistics import mean
import string

# Load data

In [ ]:
res = pd.read_excel("result-here")
res.head()

In [1724]:
answers = res["Answer"].tolist()
labels = res["Label"].tolist()
n_thought = res["n_CoT"].tolist()

# Evaluate

## F1_score

In [1725]:
def precision(answer, label):
    answer_tokens = set(answer.lower().split())
    label_tokens = set(label.lower().split())

    intersection = answer_tokens & label_tokens
    precision = len(intersection) / len(answer_tokens) if len(answer_tokens) > 0 else 0

    return precision

def recall(answer, label):
    answer_tokens = set(answer.lower().split())
    label_tokens = set(label.lower().split())

    intersection = answer_tokens & label_tokens
    recall = len(intersection) / len(label_tokens) if len(label_tokens) > 0 else 0

    return recall

def f1(answer, label):
    prec = precision(answer, label)
    rec = recall(answer, label)

    if prec == 0 and rec == 0: return 0
    return 2*prec*rec/(prec+rec)

def evaluate_f1(answers, labels):
    avg_f1 = []
    for i in range(len(answers)):
        f1_score = f1(answers[i], labels[i])
        avg_f1.append(f1_score)
    return mean(avg_f1)

In [ ]:
p, r = [], []
for i in range(len(answers)):
    ans, lab = answers[i], labels[i]
    p.append(precision(ans, lab))
    r.append(recall(ans, lab))
print(f"Precision: {mean(p)}")
print(f"Recall: {mean(r)}")

In [ ]:
evaluate_f1(answers, labels)

In [ ]:
mean(n_thought)

## GPT Score


### Initialize LLM

In [1730]:
from transformers import AutoTokenizer
from langchain_community.llms import VLLMOpenAI
from langchain_openai import ChatOpenAI

In [1731]:
inference_server_url = "your_inference_server_url"
tokenizer = AutoTokenizer.from_pretrained("Qwen2.5-7B-Instruct")

### For Chat OpenAI template
llm = ChatOpenAI(
    model="Qwen2.5-7B-Instruct",
    openai_api_key="test",
    openai_api_base=inference_server_url,
    temperature=0,
    max_tokens=100,
    streaming= False
)

### Metrics implementation

In [1733]:
class Correctness(BaseModel):
    """Correctness score ranges from 1-5 to evaluate whether the generated answer aligns with the reference answer"""
    correctness_score: int = Field(
        description="The correctness of generated answer compares to reference, score ranges from 1-5"
    )
 
class Faithfulness(BaseModel):
    """Faithfulness score ranges from 1-5 to check whether the generated answer remains true to the given context"""
    faithfulness_score: int = Field(
        description="The generated answer remains true to the given context, score ranges from 1-5"
    )

class Relevancy(BaseModel):
    """Relevancy score ranges from 1-5 to check whether the retrieved context and the generated answer relevant to the query"""
    relevancy_score: int = Field(
        description="The retrieved context and the generated answer relevant to the query, score ranges from 1-5"
    )


In [1734]:
def correctness_evaluation(query, answer, label):
    system_prompt = (
        "You are a judge. Your task is to evaluate whether the provided answer aligns with the label, given the query, "
        "by assigning a score strictly based on the following rubric (score must be 1, 2, 3, 4, or 5):\n\n"
        "Score Rubric:\n"
        "1: If the generated answer is not relevant to the user query and reference label.\n"
        "2: If the generated answer aligns with the reference label but is not relevant to the user query.\n"
        "3: If the generated answer is relevant to the user query and reference label but contains mistakes.\n"
        "4: If the generated answer is relevant to the user query and has the exact same metrics as the reference label, "
        "but it is not as concise.\n"
        "5: If the generated answer is relevant to the user query and fully correct according to the reference label.\n\n"
        "Important Notes:\n"
        "- Only evaluate based on commonalities between the answer and the label.\n"
        "- Do not penalize for elements present in the label but missing in the answer.\n"
        "\n"
        "Only return the score (1, 2, 3, 4, or 5). Do not generate any other text, such as explanations or openings/closings."
    )
    chat_template_contextual = tokenizer.apply_chat_template(
        [
            {"role": "system", "content": system_prompt},
            {"role": "user", "content": f"\nQuery: {query}\nAnswer: {answer}\nLabel: {label}"}
        ],
        tokenize=False,
        add_generation_prompt=True
    )
    prompt_gen_answer = PromptTemplate(
        template=chat_template_contextual, 
        input_variables=["system_prompt", "query", "answer", "label"]
    )
    
    structured_check_content = llm.with_structured_output(Correctness)
    chain_gen_answer = prompt_gen_answer | structured_check_content
    final_score = chain_gen_answer.invoke({
        "system_prompt": system_prompt, 
        "query": query, 
        "answer": answer, 
        "label": label
    }).correctness_score
    
    return final_score

def faithfulness_evaluation(answer, context):
    system_prompt = (
        "You are a judge. Your task is to evaluate whether the provided answer remains true and faithful "
        "to the given context by assigning a score strictly based on the following rubric:\n\n"
        "Score Rubric:\n"
        "- Score 1: The answer is completely unfaithful and contradicts the context.\n"
        "- Score 2: The answer contains mostly false information or is unsupported by the context, with only minor overlaps.\n"
        "- Score 3: The answer is partially faithful, with some alignment to the context but contains notable inaccuracies.\n"
        "- Score 4: The answer is mostly faithful to the context but may have minor inaccuracies or omissions.\n"
        "- Score 5: The answer is completely faithful and aligns fully with the context.\n\n"
        "Important Notes:\n"
        "- Only evaluate based on common elements between the answer and the context.\n"
        "- Do not penalize the answer for missing elements that are present in the context but not in the answer.\n\n"
        "Only return the score (1, 2, 3, 4, or 5). Do not generate any additional text, such as explanations or openings/closings."
    )
    chat_template_contextual = tokenizer.apply_chat_template(
        [
            {"role": "system", "content": system_prompt},
            {"role": "user", "content": f"Answer: {answer}\nContext: {context}"}
        ],
        tokenize=False,
        add_generation_prompt=True
    )
    prompt_gen_answer = PromptTemplate(
        template=chat_template_contextual,
        input_variables=["system_prompt", "answer", "context"]
    )
    structured_check_content = llm.with_structured_output(Faithfulness)
    chain_gen_answer = prompt_gen_answer | structured_check_content
    evaluation_score = chain_gen_answer.invoke({
        "system_prompt": system_prompt,
        "answer": answer,
        "context": context
    }).faithfulness_score
    
    return evaluation_score



def relevancy_score(query, context, answer):
    system_prompt = (
        "You are a judge. Your task is to evaluate the relevance of the retrieved context and the generated answer "
        "to the given query. Your evaluation must strictly follow the score rubric below:\n\n"
        "Score Rubric:\n"
        "- Score 1: Both the retrieved context and generated answer are completely irrelevant to the query.\n"
        "- Score 2: The retrieved context is somewhat related, but the generated answer is irrelevant to the query.\n"
        "- Score 3: Both the retrieved context and generated answer are somewhat relevant to the query, but not precise.\n"
        "- Score 4: The retrieved context and generated answer are mostly relevant to the query, with minor inaccuracies.\n"
        "- Score 5: Both the retrieved context and generated answer are fully relevant and precisely aligned with the query.\n\n"
        "Important Notes:\n"
        "- Only return the score (1, 2, 3, 4, or 5). Do not provide any additional text such as explanations, openings, or closings."
    )
    chat_template_contextual = tokenizer.apply_chat_template(
        [
            {"role": "system", "content": system_prompt},
            {"role": "user", "content": f"Query: {query}\nContext: {context}\nAnswer: {answer}"}
        ],
        tokenize=False,
        add_generation_prompt=True
    )
    prompt_gen_answer = PromptTemplate(
        template=chat_template_contextual,
        input_variables=["system_prompt", "query", "context", "answer"]
    )
    structured_check_content = llm.with_structured_output(Relevancy)
    chain_gen_answer = prompt_gen_answer | structured_check_content
    relevancy_result = chain_gen_answer.invoke({
        "system_prompt": system_prompt,
        "query": query,
        "context": context,
        "answer": answer
    }).relevancy_score
    
    return relevancy_result


### Execution

In [1783]:
def run_evaluate(tasks):
    query, label, answer, context = tasks[0], tasks[1], tasks[2], tasks[3]
    try:
        corr = correctness_evaluation(query, answer, label)
        faith = faithfulness_evaluation(answer, context)
        rele = relevancy_score(query, context, answer)
        result = {"Correctness": corr, "Faithfulness": faith, "Relevancy":rele}

        return result
    except Exception as e:
        print(f"Error occurred during processing question '{query}': {e}")
        return None
        
        